In [1]:
import pandas as pd
import os

In [3]:
# Load the CSV file with row 1 as the header
df = pd.read_csv('pbp-2023.csv', header=0)
print(df.head(3))
base_dir = r'C:\users\jchbe\downloads\footballplays\23'

       GameId    GameDate  Quarter  Minute  Second OffenseTeam DefenseTeam  \
0  2023110503  2023-11-05        2      12       5         CLE         ARI   
1  2023110504  2023-11-05        2       3      53          LA          GB   
2  2023110504  2023-11-05        2       3      15          LA          GB   

   Down  ToGo  YardLine  ...  IsTwoPointConversion  \
0     3     5        56  ...                     0   
1     1    10        55  ...                     0   
2     2     2        63  ...                     0   

   IsTwoPointConversionSuccessful  RushDirection  YardLineFixed  \
0                               0            NaN             44   
1                               0            NaN             45   
2                               0         CENTER             37   

  YardLineDirection  IsPenaltyAccepted  PenaltyTeam  IsNoPlay  PenaltyType  \
0               OPP                  0          NaN         0          NaN   
1               OPP                  0       

In [5]:
# Extract unique values from 'GameId' column
#unique_game_ids = df['GameId'].unique()
# Convert all values in 'GameId' column to strings and store them in a dictionary
gameid_list = df['GameId'].astype(str).tolist()

#print(gameid_list)

if '2023111211' in gameid_list:
    print("win")
else:
    print("lose")

win


In [7]:
# Step 1: Define the conversion dictionary
team_conversion_dict = {
    'KC': 'Chiefs',
    'CAR': 'Panthers',
    'DEN': 'Broncos',
    'DAL': 'Cowboys',
    'LAR': 'Rams',
    'LV': 'Raiders',
    'PIT': 'Steelers',
    'NYG': 'Giants',
    'SF': 'Forty-Niners',
    'CIN': 'Bengals',
    'WAS': 'Commanders',
    'BUF': 'Bills',
    'CHI': 'Bears',
    'ATL': 'Falcons',
    'TB': 'Buccaneers',
    'PHI': 'Eagles',
    'SEA': 'Seahawks',
    'TEN': 'Titans',
    'NO': 'Saints',
    'LAC': 'Chargers',
    'ATL': 'Falcons',
    'NYJ': 'Jets',
    'NE': 'Patriots',
    'ARI': 'Cardinals',
    'MIA': 'Dolphins',
    'HOU': 'Texans',
    'IND': 'Colts',
    'DET': 'Lions',
    'CLE': 'Browns',
    'BAL': 'Ravens',
    'JAX': 'Jaguars',
    'GB': 'Packers',
    'MIN': 'Vikings'
}

yard_conversion_dict = {
    'OPP': 'opposing',
    'OWN': 'own'
}

# Step 2: Define the function
def convert_abb(abbr):
    # Look up the abbreviation in the dictionary, return "Unknown" if not found
    return team_conversion_dict.get(abbr.upper(), "Unknown")

def convert_yarddir(abbr):
    # Look up the abbreviation in the dictionary, return "Unknown" if not found
    return yard_conversion_dict.get(abbr.upper(), "Unknown")

print(convert_abb('JAX'))
print(convert_abb('DET'))
print(convert_abb('KC'))

Jaguars
Lions
Chiefs


In [11]:
def gen_phrase(offTeam, defTeam, down, togo, desc, type, formation, yard, yarddesc):
    myline = f"American Football, Coaches Film, {offTeam} offense against {defTeam} defense, "
    if(type == 'rush'):
        myline = myline + f"rushing "
    if(formation == 'under center'):
        myline = myline + f"under center "
    myline = myline + f"{desc} at {yarddesc} {yard} yard line"
    return myline
    

In [16]:
base_dir = r'C:\users\jchbe\downloads\footballplays\23'

In [20]:
# Sort values in the 'GameId' column in ascending order and display them
unique_values_series = pd.Series(df['GameId'].unique()).sort_values().reset_index(drop=True)
print(unique_values_series)


0      2023090700
1      2023091000
2      2023091001
3      2023091002
4      2023091003
          ...    
267    2024010709
268    2024010710
269    2024010711
270    2024010712
271    2024010713
Length: 272, dtype: int64


In [17]:
exclude_phrases = ["TIMEOUT", "END QUARTER", "END GAME", "TWO-MINUTE"]
for (root,dirs,files) in os.walk(base_dir, topdown=True):
    baseName = os.path.basename(root)
    #print(baseName)
    if baseName in gameid_list:
        output_list = []
        #print(baseName + "in list we are in")
        # Filter rows with the specific GameId
        filtered_df = df[df['GameId'].astype(str) == baseName]
                # Filter the DataFrame
        onlydowns_df = filtered_df[
           # (df['IsNoPlay'] == 0) &  # 'IsNoPlay' must be zero
            (~df['Description'].str.contains("TIMEOUT|TWO-MINUTE|END GAME|END QUARTER", case=False, na=False))  # Exclude specific words in 'Description'
        ]
        # Sort by 'Quarter' ascending, 'Minute' descending, 'Second' descending
        sorted_df = onlydowns_df.sort_values(by=['Quarter', 'Minute', 'Second'], ascending=[True, False, False])
        for index, row in sorted_df.iterrows():
            phrase = gen_phrase(
                convert_abb(row['OffenseTeam']),
                convert_abb(row['DefenseTeam']),
                row['Down'],row['ToGo'],
                row['Description'].lower(),
                str(row['PlayType']).lower(),
                str(row['Formation']).lower(),
                row['YardLineFixed'],
                convert_yarddir(row['YardLineDirection'])
                               )
            
            output_list.append(phrase)

        print(output_list)
        filename = "captions.txt"
        file_path = os.path.join(root, filename)
        with open(file_path, "w") as file:
            for sentence in output_list:
                file.write(sentence + "\n")


C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[
C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[


['American Football, Coaches Film, Lions offense against Chiefs defense, under center 7-h.butker kicks 65 yards from kc 35 to end zone, touchback. at opposing 35 yard line', 'American Football, Coaches Film, Lions offense against Chiefs defense, rushing under center (15:00) 5-d.montgomery right guard to det 32 for 7 yards (32-n.bolton; 56-g.karlaftis). at own 25 yard line', 'American Football, Coaches Film, Lions offense against Chiefs defense, under center (14:29) 16-j.goff pass incomplete short right. at own 32 yard line', 'American Football, Coaches Film, Lions offense against Chiefs defense, (14:25) (shotgun) 16-j.goff pass incomplete deep right to 8-j.reynolds. at own 32 yard line', 'American Football, Coaches Film, Lions offense against Chiefs defense, (14:21) 3-j.fox punts 61 yards to kc 7, center-47-s.daly. 17-r.james to kc 13 for 6 yards (30-k.dorsey). at own 32 yard line', 'American Football, Coaches Film, Chiefs offense against Lions defense, rushing (14:09) (shotgun) 25-c.e

C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[
C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[


['American Football, Coaches Film, Ravens offense against Texans defense, under center 15-k.fairbairn kicks 67 yards from hou 35 to bal -2. 13-d.duvernay to bal 28 for 30 yards (23-e.murray). penalty on bal-26-g.stone, illegal block above the waist, 8 yards, enforced at bal 16. at opposing 35 yard line', 'American Football, Coaches Film, Ravens offense against Texans defense, rushing (14:54) (shotgun) 27-j.dobbins left tackle to bal 12 for 4 yards (51-w.anderson; 96-m.collins). at own 8 yard line', 'American Football, Coaches Film, Ravens offense against Texans defense, under center (14:22) 8-l.jackson pass short right to 80-i.likely to bal 16 for 4 yards (24-d.stingley). at own 12 yard line', 'American Football, Coaches Film, Ravens offense against Texans defense, (13:44) (shotgun) 8-l.jackson sacked at bal 9 for -7 yards (52-j.greenard). at own 16 yard line', 'American Football, Coaches Film, Ravens offense against Texans defense, (13:00) 11-j.stout punts 67 yards to hou 24, center-6

C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[
C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[


...

C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[
C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[


['American Football, Coaches Film, Bears offense against Saints defense, under center 19-b.grupe kicks 65 yards from no 35 to end zone, touchback. at opposing 35 yard line', 'American Football, Coaches Film, Bears offense against Saints defense, (15:00) (shotgun) 17-t.bagent pass short middle to 11-d.mooney to chi 38 for 13 yards (32-t.mathieu). at own 25 yard line', 'American Football, Coaches Film, Bears offense against Saints defense, under center (14:28) 17-t.bagent pass short middle to 2-d.moore to no 46 for 16 yards (29-p.adebo). at own 38 yard line', 'American Football, Coaches Film, Bears offense against Saints defense, (14:01) (no huddle, shotgun) 17-t.bagent pass incomplete short right. at opposing 46 yard line', 'American Football, Coaches Film, Bears offense against Saints defense, rushing under center (13:56) 21-d.foreman right tackle to no 38 for 8 yards (94-c.jordan; 56-d.davis). at opposing 46 yard line', 'American Football, Coaches Film, Bears offense against Saints de

C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[
C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[


['American Football, Coaches Film, Giants offense against Raiders defense, under center 2-d.carlson kicks 58 yards from lv 35 to nyg 7. 0-p.campbell to nyg 20 for 13 yards (22-a.abdullah). at opposing 35 yard line', 'American Football, Coaches Film, Giants offense against Raiders defense, (14:55) (shotgun) 8-d.jones pass incomplete short left to 26-s.barkley. at own 20 yard line', 'American Football, Coaches Film, Giants offense against Raiders defense, (14:51) (shotgun) 8-d.jones pass incomplete short left to 17-w.robinson. at own 20 yard line', 'American Football, Coaches Film, Giants offense against Raiders defense, (14:44) (shotgun) 8-d.jones pass short middle to 82-d.bellinger to nyg 29 for 9 yards (25-t.moehrig, 56-a.burney). at own 20 yard line', 'American Football, Coaches Film, Giants offense against Raiders defense, under center (14:03) (run formation) penalty on nyg-73-e.neal, false start, 4 yards, enforced at nyg 29 - no play. at own 29 yard line', 'American Football, Coach

C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[
C:\Users\jchbe\AppData\Local\Temp\ipykernel_28820\1076361920.py:11: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  onlydowns_df = filtered_df[


In [86]:
#weeks: 16 + 16 + 16 + 16 -> 14: 78 -> 15:93 -> 7.13:106 -> 8.16:122 -> 9.14: 136 -> 10.14: 150
# 11.14: 164 -> 12.16 180  -> 13.13:   193 -> 14.15: 208 ->   15.16: 224  ->    16.16:240     ->  17.16:  256 -> 18.16: 272
# Loop through the first 16 rows of the DataFrame

#for row in unique_values_series[256:272]:
#    # Use a specific column value (e.g., 'GameId') as the folder name
#    folder_name = str(row)  # Convert to string if necessary
#    folder_path = os.path.join(cur_dir, folder_name)
#    
#    # Create the directory
#    os.makedirs(folder_path, exist_ok=True)
#    print(f"Created directory: {folder_path}")

In [ ]:
#lastvalue
#print(unique_values_series[116:130])
#11print(unique_values_series[150:164])
#print(unique_values_series[260:272])
#for row in unique_values_series[16:32]:
#    print(row)